# Math 124 - Programming for Mathematical Applications
Per-Olof Persson, UC Berkeley

## Homework 10

In [ ]:
using Plots

### Problem 1 - Data Structures and a 5th-Order Runge-Kutta Solver

In this problem, we'll build a robust framework for solving Initial Value Problems (IVPs). First, we'll create custom data structures to neatly package our problem definitions and their corresponding solutions. This is a great programming practice that makes our code much cleaner and easier to manage.

#### Problem 1(a): Defining our Structures

Define a `struct` named `IVPproblem` to hold the definition of an IVP. It should contain:

* `f`: The function $f(t, y)$ defining the ODE $y' = f(t, y)$, with type `Function`.
* `T`: The final time of the integration, with type `Number`.
* `y0`: The initial condition vector $y(0)$, with type `Vector`.

Next, define a `struct` named `IVPsolution` to store the output of our solver:

* `t`: A `Vector` containing the time points of the solution.
* `y`: A `Matrix` where each **column** corresponds to the solution vector $y(t)$ at a time point in `t`.

#### Problem 1(b): Implementing the `runge5` Solver

Next, implement the following 5th-order accurate Runge-Kutta method. This is a "higher-order" method, meaning it's generally more accurate for a given step size $h$ than methods like RK4. 

Create a Julia function `runge5(f, y0, h, N, t0=0)` with the same syntax as the `rk4` function from our lecture notebook. This function will perform `N` steps of size `h`.

The formulas for the stages ($k_i$) and the final step are:

$$
\begin{align*}
k_1 &= h f(t_n, y_n) \\
k_2 &= h f(t_n + h/5, y_n + k_1/5) \\
k_3 &= h f(t_n + 2h/5, y_n + 2k_2/5) \\
k_4 &= h f(t_n + h, y_n + 9k_1/4 - 5k_2 + 15k_3/4) \\
k_5 &= h f(t_n + 3h/5, y_n - 63k_1/100 + 9k_2/5 - 13k_3/20 + 2k_4/25) \\
k_6 &= h f(t_n + 4h/5, y_n - 6k_1/25 + 4k_2/5 + 2k_3/15 + 8k_4/75) \\
y_{n+1} &= y_n + (17k_1 + 100k_3 + 2k_4 - 50k_5 + 75k_6) / 144
\end{align*}
$$

#### Problem 1(c): Creating a "Convenience" Method

Now we'll see the benefit of our new data structures. Implement a new *method* for `runge5` that takes our `IVPproblem` struct as an argument. This is a classic example of **multiple dispatch** in Julia.

Implement `runge5(ivp::IVPproblem, N)`. This function should:
1.  Take an `ivp` of type `IVPproblem` and `N` (the number of timesteps) as input.
2.  Call the `runge5` function from 1(b), extracting the `f`, `y0`, and `T` fields from the `ivp` object. Remember to calculate the step size `h = T / N`.
3.  Return the result packaged neatly as an `IVPsolution` struct.

**Important:** Do not rewrite any of your integration logic! This function should just be a thin "wrapper" that calls your previous function.

#### Problem 1(d): Testing the Solver

Let's test our new solver and data structures on a simple problem we know the answer to: the scalar ODE $y' = -y$ with $y(0) = 1$. The true solution is $y(t) = e^{-t}$.

* Create an `IVPproblem` for this differential equation, with $T=1$ and initial condition $y_0 = [1.0]$. (Remember, `y0` must be a `Vector`!)
* Solve the problem using your new `runge5` method with $N=10$ steps. This will return an `IVPsolution`.
* Compute the error: the difference between your computed solution (in `sol.y`) and the true solution $e^{-t}$ (evaluated at the time points in `sol.t`).
* Display the error vector.

### Problem 2 - The Chaotic Double Pendulum

Now for a much more exciting (and chaotic!) problem: the double pendulum. We'll use our `runge5` solver to simulate its motion.

The state of the pendulum at time $t$ is given by two angles, $\theta_1(t)$ and $\theta_2(t)$, as shown in the figure.


<div>
<img width=250 src="data:image/png;base64,iVBORw0KGgoAAAANSUhEUgAAAmMAAAJWCAAAAAAxFN+/AAAACXBIWXMAABcRAAAXEQHKJvM/AAAR
uElEQVR42u3dfYhs913H8a/eYGq84FOMI1FChWr+0JVQoxafShhJaah/NGqdSoJFUaQwYsU+iA8M
Ra0PaHBTQfJHW2UsilYkTn2oRSnTGhotOv1DSbkd09RIpgZLuwm3Gevxj5ndvffuzM7OnvOdnTPn
9f4nJ3d2Hnb2zff85vM5c04UQC7hLQDHwDGAY+AYOAZwDBwDxwCOgWPASsdiS/A34RjHwDFwjGMc
4xg4Bo5xDBzDRThWxYNFRMTYu4pkxzreVSQ61o6IGHlbkefYOCJiz9uKPMeKTkTE0PuKPMcmERGt
qTcWaY4VvYiIvjcWeY4dGGRIdKwoiqLoR0T0vLPIc2zaiog48NYizbHZIOt6a5HnWLGnUUKyY0ON
EpIdKzRKyHZMo4RsxzRKSHdMo4RsxzRKSHdMo4RsxzRKSHLseHBplJDi2LVfKtIoIdsxjRLSHdMo
IdsxjRLSHdMoIdsxjRLSHdMoIdsxjRLSHdMoIdsxjRLSHdMoIduxYqBRQvZpCzVKyHZMo4T00692
NEocS0ajxLH0Z+hERAy80xzLQxDLsXQ0ShxLH2StiGgJYjmWiEaJY9lolDiWzkAQy7FsNEocq2yv
uOTfNUocq+rBlj6aQ/s5lu2YRolj2Y5plDiW7phGiWPZjmmUOJbumEaJY9mOaZQ4lu6YRolj2Y5p
lDiW7tjwJo0SxxIdmw72IgwyjqU5NtlvRUTnVRoljqVwMGhHRHTGGiWOJQoWvUlRaJQ4VjWTYW+2
COsO5yWSRolj1Y2v8aDbiusFKwqNEsdK0+/vdzqdzmz3GBHt/dH1Q0ujxLHSHyyP6fRHC3aKGiWO
laPT6XQ6/X5/MF42qjRKHEtHo8SxdHxHiWPZ+I4Sx9LxHSWOZaNR4lgJzpbga5Q4dv4HO9ujaZQ4
lu2YRolj6Y5NNUocS3ZMo8SxdMdmjdLE28+xNMcEsRxLd0yjxLF0x0YREW3vP8fyHNMocSzdMY0S
x7IdK7qCWI5V5dgTf/Xef1/wzxoljlXE3991f//dP7D3/pO3aJQ4VgnvvPSWoiiKN3/hO0/c5NB+
jlXBR26+/WpRFMXnbrv5X0/cqFHiWAV8X/zMbOMn41VLBplGiWNl+GjEn8223hHxiRM3a5Q4Vpq3
Rjwx2/pAxMMnb9cocaws7YjnZlsfi3jg5O0aJY6V5fa4PN/6ZMTdC35Ao8SxclyNuG2++UzE1yz4
CY0Sx8rxqYhbH53xrjgaadehUeJYKf4j4kX3znh5xKVFP6JR4lgprkTcMd98MuKWhT+jUeLYWtww
j56OuH2++fGIr1p8F40Sx9Z5sBse7fljsf4t4hsX30mjxLESjhW3Hu0gPxxxX3HKINMocex8jt0T
8fxs628i3rDkXholjpVwrBdxZbb1rohHl91No8Sx8zv22NH5eX4pblm6rtcocez8jhV3xy/MNu6L
7vL7aZQ4dn7H/i6+4X+Loij++4u/4j+X30+jxLHzO1a8Nn6lKIr/e/Dm9552R40Sx87v2NWfvfz9
b3/ou779w6feUaPEsfM7VhQvPP6Xf3vl2n944oGPnPghjRLHSjh2A1dedykeO/GvGiWOVebYR//g
T2OBYxoljlXJly1yTKPEsQq5dZFjGiWOpTumUeJYumNjjRLHkh3TKHEs3TGNEseyHRPEcizdMY0S
x7IdK/YjIvb9UTiW55hGiWPZjmmUOFYNX77csakglmMrOMt6/dmI9y29UaPEsRUPtvrRnvz5uyLu
/Ll/WHa7Qcaxso6tQhDLsWzHNEocS3dsNsgEsRzLc0yjxLF0xzRKHMt2TKPEsXTHNEocy3ZMo8Sx
dMc0ShzLdkyjxLF0xzRKHEtHo8SxdDRKHNvMIBPEciwRjRLHstEocSwdjRLHstEocSwdjRLH0geZ
IJZj2WiUOJaOQcaxbDRKHFuwhqr2xWmUOHbiwSqeiholjmU7plHiWLpjGiWOZTumUeJYumMaJY5l
O6ZR4li6Y4JYjqU7plHiWLZjRTsiYuQvxbE8xzRKHMt2TKPEsXTHJoJYjmWjUeJYNholjqUjiOVY
Nholjm1mkHX9tTiWiEaJY9lolDiWjkaJY9lolDiWjkaJY9lolDiWjkaJY9lolDiWjkaJY9lolDi2
mUGmUeJYJholjmWjUeJYOholjmWjUeJYOholjmWjUeJYOholjmWjUeJYOholjmWjUeLYZgaZRolj
mWiUOJaNRolj6WiUOJaNRolj6WiUOJaNIJZj6WiUOJY+yFoGGceS0ShxLBuNEsfSGQhiOZaNRolj
2WiUOJaOIJZj2WiUOLaZQTbwJ+RYHholjqWjUeJY+iBrRURLEMuxRDRKHMtGo8SxdDRKHEtHo8Sx
bDRKHEtHo8SxbDRKHNvMINMocSwRjRLH0tEocSx9kGmUOJaNRolj2WiUOJaORolj6WiUOJaNRolj
6WiUOJaNRoljmxlkGiWOJaJR4lg6GiWOpQ8yjRLHstEocSwbjRLH0hHEciwdjRLHshkZZBzLRqPE
sWw0ShxLpyuI5VgyGiWOpaNR4lg2gliOpaNR4thmBtnE35VjeWiUOJaORolj2YwiItr+sBxLRKPE
sWw0ShxLR6PEsWw0ShxLR6PEsWw0ShxLR6PEsc0MMo0SxxLRKHEsHY0Sx7LRKHEsHY0Sx7LRKHEs
HY0Sx7LRKHEsHY0Sx7LRKHEsHY0SxzYzyDRKHEtEo8SxdDRKHMtGo8SxdDRKHMtGo8SxdDRKHMtG
o8SxdPYNMo4lo1HiWDoaJY6lD7I9jRLHktEocSwdjRLHshHEciwdjRLHNjPIBLEcS2R2aP+k32lH
RHR6Q75xrGIOIiJuimvoSmU5Vi37cYKeWcaxKnnopGPRkstyrDKmnVhEy0dNjlVFN5Yw9vfnWNZi
7HCSWflzrApGsRzfJ+FYFeyd4pj0n2MVMDxNMTUmx7LHmEHGsfIcnK5YdCnAsZIMVjjWogDHStJZ
4ZiMjGPpjo04wLGSv98qfPeSYxzjGMfQcMf2VjkmIOOYz5Uc23J6qxxz6AXHSjJaoZgjLzhWmpYl
P8cudmdpV8mx0qwoxdvW/BwrTX/Fimzfl+A4VpJpe4Vke0YZx0oyWbrsf+XhQWRGGcfKMW4tOz5x
PJ9xLUdfcCxjkvWuXa11fMDkWLk1WWfpt8Qn85taAzJwrNz+cm/pKVUG8ynXcQIMjpVj1DvaY7YH
1+0ZDzpCf45VtS4bD/r90fjk0mvUEmNwLHvB1pXIcmxTC7Y9MQbH0kbZvkSWY+mjrO3kdxzLRiLL
sfxPnhJZjqVzmMi2JbIcOycr94ISWY6V/H3P8AtLZDmW7Vgx7UlkOZbrmESWY/mOSWQ5lu5YUUwk
shxLdkwiy7F8x45iDIksx7Ick8hyLN+x4uDwwLK+tT/HchyTyHIs3zGJLMfSHTtOZH3Vl2NpTH9V
IsuxZMf24ovEGBzLpBsxlMhyLJFBRO+aRNaBZRyrmklEe1oUElmOZXHQitZcKoksx1LW++1rL0Yi
keVYsmLXHFgmkeVYRXTmJ8M7RiLLsUrpnVCsKKZ9iSzHqlRs0VXtj46RlchyrORarHuYWpyg35LI
cmxZErHecr+9bHcokeXYst/37L/wpL1gLXYNElmOlXRs0orYX7krFWNw7NyODVpnuA60RJZj53Zs
2j1b/nWUyPaMMo6t5di4deZllkSWY+dxbH+dNdZxIivG4NgZHRu315xKElmOreXYQS8iOmuuriSy
HDuzY9P++eaRky9y7IyODVrnTruGElmOrXTsoL9XZuUukeXYCsdG3YiIzrjEY4/2JLIcWzrC9lsR
Ed2SGZdElmNLxs/+XkTEXr+CD4USWY6dGGDD7myt3qtq/yaR5diRXeN+7/AQsN6wwn2bRLbpjo37
/X6n0zm+uni7X3nY4ALlzXZscM116zu9/jhljyaRbfYca3U6nV6/PxinrpeOElkxhs+VWUhkOZaP
RJZj+aPM5XA4lr/4k8hyLB0nXyx8hzcbiazjLlby2Q/++fAzZZ5RIsuxU3n+p1/ytvf8+kteX2b6
NT6R5dhpfOaur/5EURRP3fotpUbZqNmJLMdO4wfj4aIoiuJ34odLPWuzE1mOncIH46Zni6Ioiv+K
+KdyzztucCLLsVO4P755vnVH/FjJJ25wIsux5Vy9HK+db94Tt32+7FOP2w1NZDm2nGHEG+ebPxJx
pfyTNzSR5dhyHon4rfnmj0dUEaJOGnmBco4t5y0Rvzff/KmI36/k+Zt48kWOLef1Ed1HZ9x7PNJK
0sBElmPL+dGIb7p3xtdGvLWql9C4ky867mI5D0S8Y775uojfqOxxm5bIcmw5PxHxyHzzwYi3V/jI
R4nsiGPN5o3HYr0m4t1VPnSjElmOLefh4x3kKyMer/bBjxLZIccazAeOM9iXxRd8uuqHb0wiy7Hl
XH1RPDDffHG8tPrHb0oiy7FTeEXcPdv43E3xyxlP0IxElmOnKRA3z/Zjj8fNT6c8w/EFyjnWUL47
/nD+CfNNWU/RgESWY6fxL7fc8XRRFKMvuScvYpj2dj2R5dipDF/a+sVH3vB1b34h80l2PZHl2Ao+
+f6/eOy5o/979k3fc+cPva/yUbbbiazv8K7DP94elyISFmc7/VVfx12swf+8eP+zVz/0soi/rv6F
7XAiy7E1eNtDRVEUz319PJgxYHf2AuUcW4PXzJZLv5YR+he7m8hybA0+NfvPH8crktaKR4nslGMN
dWzOb8dvZr28nUxkObY+911+Ju317WIiy7G1efLS72a+wt07+SLH1ub+V38+9SXuXCLLsXX5k297
LvtF7lgiy7E1+efveHYDL3OnLlDOsfX42Pc+s5HXuUuJLMfW4qmXP1UURVF86IX0V7o7iazjLtZb
KH18tsN89QaebLoriSzH1uDTd11utVqt1pfGH23k+XYkkeXYGnzn4VUJv/LqZp7wKMaodSLLse1m
FxJZjm050/pfoJxjNfigUfNElmM1oOaJLMfqQL1PvsixelDnRJZjdVn71/fkixyrDbVNZDlWo1F2
mMj2phzb6uVznV98PRNZx13Ua5TVMZHlWM2oYSLLsdoxqFsiy7EaLilrlshyrI4Ma5XIcqyea/86
JbIcqymj+lygnGO1HWW1+aovx+pLXRJZjtWZepx8kWO1phaJLMdqzlEiO+EYktj+RJZj9ecokR1z
DElseSLLsZ1gqxNZju3IKNviRJZju8LRBcpHHEMW25rIcmyH2NILlHNsp9jKRJZju8U2JrIc2zVG
W5fIcmzn2LpE1nd4d5Atu0C54y52cpRtVSLLsR0dZYeJ7JBjHMtiexJZju0sW5PIcmyH2ZKTL3Js
pz9Eb0Uiy7HdZhtOvsixHWcLElmO7TwXnshyrAGj7IITWY41gcmFJrIcawYXmcg67qIhHFxcIsux
xnBhiSzHGjTKuheTyHKsSVxMIsuxRjHtLU1kp+Nhv98fjqccQzkWn3xxOjhsNiPagwOOodQoO5nI
Tg8v9Dun1Z9yDGW48eSL4+sNq/yEBhxrItclssNYxIBjKBdjHCay/WI/FtPjGMpxmMh+ayxjyDGU
HGXdWMGYYyjJqHW6Y3scQ2UxRu7ekmON5s5NDDKONZnJihXZiGMoyYp9ZUX5BceazF5sYtXPsSaz
Kr0IjqHk58qVjk04hlKMYyMxLMc4xjFcWHTBMeSv+accg8+V2G5WHXrR5RhKMlzh2IBjKMmqgOyA
YyhLbwN1JccaPsha+WOMYw2nf4piVZ0Wg2MNp7NUsXbBMVSyt2wvO65nyjFUw8FiySo8SxnHTLJF
SWyVpyfmGIrhjcfDVntuYo6hKKb9ay3bq/a0PRzDjMl+pxMRnc5+5aeL5Riy4Rg4Bo4BHAPHwDGA
Y+AYOAZwDBwDOAaOgWMAx8AxcAzgGDgGcAwcA8cAjoFj4BjAMXAM4Bg4Bo4BHAPHwDGAY+AYwDFw
DBwDOAaOgWMAx8AxgGPgGDgGcAwcA8cAjoFj4BjAMXAM4Bg4Bo4BHAPHwDGAY+AYwDFwDBwDOAaO
gWMAx8AxgGPgGDgGcAwcA8cAjoFjAMfAMXAM4Bg4hibw//5VIvNUuSK7AAAAAElFTkSuQmCC"/>
</div>

Assuming unit lengths ($L_1=L_2=1$), unit masses ($m_1=m_2=1$), and unit gravity ($g=1$), the equations of motion (derived from the Lagrangian) are a pair of coupled second-order ODEs:

$$
\begin{align}
\theta_1''&=\frac{-3\sin\theta_1-\sin(\theta_1-2\theta_2)
-2\sin(\theta_1-\theta_2)\cdot(\theta_2'^2+\theta_1'^2\cos(\theta_1-\theta_2))}
{3-\cos(2\theta_1-2\theta_2)} \label{ode1} \\ 
\theta_2''&=\frac{2\sin(\theta_1-\theta_2)(2\theta_1'^2+2\cos\theta_1
+\theta_2'^2\cos(\theta_1-\theta_2))}{3-\cos(2\theta_1-2\theta_2)} \label{ode2}
\end{align}
$$

#### Problem 2(a): Converting to a First-Order System

Our `runge5` solver (like most standard solvers) only works for *first-order* systems ($y' = f(t,y)$). We need to convert these two second-order equations into a system of four first-order equations.

We do this by introducing **state variables**. Let's define:
* $y_1 = \theta_1$ (angle of first pendulum)
* $y_2 = \theta_2$ (angle of second pendulum)
* $y_3 = \omega_1 = \theta_1'$ (angular velocity of first pendulum)
* $y_4 = \omega_2 = \theta_2'$ (angular velocity of second pendulum)

Our state vector is $y = (y_1, y_2, y_3, y_4) = (\theta_1, \theta_2, \omega_1, \omega_2)$.

Now, we need to find the function $f(t, y)$ such that $y' = f(t, y)$. This means we need the derivatives of our state variables: $y' = (y_1', y_2', y_3', y_4')$. We already know two of the components from our definitions:

* $y_1' = \theta_1' = \omega_1 = y_3$
* $y_2' = \theta_2' = \omega_2 = y_4$

The other two come from the equations of motion given above:
* $y_3' = \omega_1' = \theta_1''$ (use the first big equation)
* $y_4' = \omega_2' = \theta_2''$ (use the second big equation)

Write a Julia function `fpend(t, y)` that takes the time `t` (which is not actually used in $f$, but the solver's function signature requires it) and the 4-element state vector `y`, and returns the 4-element derivative vector $y'$.

#### Problem 2(b): Simulating the Pendulum

Now, let's run the simulation!

* Create an `IVPproblem` for the double pendulum using `fpend`. 
    * Use the initial condition $y(0) = (\theta_1, \theta_2, \omega_1, \omega_2) = (2, 2, 0, -1)$.
    * Set the final time to $T=100$.

* Solve the IVP using `runge5` with $N=1000$ steps. This should return an `IVPsolution`.

* Plot the solution vs. time. Your plot should show all four state variables ($\theta_1(t)$, $\theta_2(t)$, $\omega_1(t)$, and $\omega_2(t)$) on a single graph. Don't forget to add labels, a title, and axis labels!

#### Animation (Optional, but highly recommended!)

If you want to, run the cell below to define an `animate` function. This function will create a movie of the evolving double pendulum and save it as a GIF. It looks pretty cool, and is a great way to visually check if your simulation is plausible.

To create the animation, call the `animate` function with your `IVPsolution` (`sol2`) as the only argument in the next cell. 

*(This relies on the `Plots` package, which we loaded at the top of the notebook.)*

In [ ]:
function animate(sol::IVPsolution)
    # Create an animation object
    anim = Animation()

    # Loop through every time step in the solution
    # size(sol.y, 2) gives the number of time steps (N+1)
    @info "Generating animation frames..."
    for i = 1:size(sol.y,2)
        # Get the angles at the i-th time step
        θ1,θ2 = sol.y[1:2,i]
        
        # Convert angles to (x, y) coordinates (physics/math standard)
        # x = L*sin(θ), y = -L*cos(θ) (with L=1)
        # p1 is the position of the first mass (end of the first rod)
        p1 = [sin(θ1), -cos(θ1)]
        # p2 is the position of the second mass (relative to p1)
        p2 = p1 + [sin(θ2), -cos(θ2)]
    
        # Create the plot for this frame
        # We set axes and limits to keep the view stable
        plot(aspect_ratio=:equal, legend=false, 
             xlims=[-2.2,2.2], ylims=[-2.2,2.2], 
             title="Double Pendulum (t=$(round(sol.t[i], digits=1)))",
             border=:none) # Hide axes for a cleaner look
        
        # Plot the rods: (0,0) -> p1 -> p2
        plot!([0,p1[1],p2[1]], [0,p1[2],p2[2]], linewidth=3, color=:black)
        # Plot the two masses
        scatter!([p1[1],p2[1]], [p1[2],p2[2]], markersize=8, color=:blue)
    
        # Add this plot as a frame to the animation
        frame(anim)
    end
    
    # Save the completed animation as a GIF
    gif(anim, "double_pendulum_animation.gif", fps=15)
end

In [ ]:
# This will take a moment to run as it generates 1001 frames and saves a GIF
animate(sol2)  # Replace `sol2` with the `IVPsolution` from your pendulum simulation